<a href="https://colab.research.google.com/github/eduartheinen/foursquare-tips/blob/master/foursquare_tips_lstm.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#**TODO/Table of Contents:**
1. [x] **Data Preprocessing**
2. [x] **Feature Engineering:**
>BOW, TF-IDF, LSA, Class-Balanced Loss;
3. [x] **ML Models:**
>Naive Bayes, SVM, XGBoost;
4. [X] **Deep Learning Models:**
> Bi-LSTM
>
> ~~BERT fine tunning~~ (future work);
5. [x] **GridSearch:**
> Cross validated combination of best parameters and features;
6. [X] **Plot and Discuss Results**
> visualize  accuracy, precision, recall and f1 metrics with box plots for each model and configuration, Confusion-Matrix
7. [ ] **EMOJIS**
8. [ ] **Análise de Frequência de Termos -- Classes Positiva e Negativa**
> Comparação antes e depois tf-idf
9. [ ] **Nuvem de Palavras**
10. [ ] **Comparação bi-tri-gramas**
11. [ ] **Apresentar predição**
12. [X] **Artigos para sustentar escolhas**
13. [ ] **Explicar diferença entre modelos**

In [34]:
!pip install -U spacy setuptools wheel xgboost plotly chart-studio # ipyml transformers
!python -m spacy download pt_core_news_sm # comment this line after first run

Requirement already up-to-date: spacy in /usr/local/lib/python3.7/dist-packages (3.0.3)
Requirement already up-to-date: setuptools in /usr/local/lib/python3.7/dist-packages (54.0.0)
Requirement already up-to-date: wheel in /usr/local/lib/python3.7/dist-packages (0.36.2)
Requirement already up-to-date: xgboost in /usr/local/lib/python3.7/dist-packages (1.3.3)
Requirement already up-to-date: plotly in /usr/local/lib/python3.7/dist-packages (4.14.3)
Requirement already up-to-date: chart-studio in /usr/local/lib/python3.7/dist-packages (1.1.0)
2021-03-01 03:39:29.527467: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcudart.so.10.1
✔ Download and installation successful
You can now load the package via spacy.load('pt_core_news_sm')


In [35]:
# uncomment only if using BERT
# !wget https://neuralmind-ai.s3.us-east-2.amazonaws.com/nlp/bert-base-portuguese-cased/bert-base-portuguese-cased_pytorch_checkpoint.zip
# !wget https://neuralmind-ai.s3.us-east-2.amazonaws.com/nlp/bert-base-portuguese-cased/vocab.txt -P bert_checkpoint/
# !unzip bert-base-portuguese-cased_pytorch_checkpoint.zip -d bert_checkpoint/

In [36]:
import re
import string
from collections import Counter

import numpy as np
import pandas as pd
import plotly.graph_objects as go
import spacy
import torch
import torch.nn as nn
import torch.nn.functional as F
from plotly.subplots import make_subplots
from sklearn.decomposition import TruncatedSVD
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics import accuracy_score, precision_score, f1_score, recall_score
from sklearn.model_selection import KFold
from sklearn.naive_bayes import ComplementNB
from sklearn.svm import LinearSVC
from torch import optim
from torchtext.vocab import Vocab
from tqdm.notebook import tqdm
from xgboost import XGBClassifier

#**0. Foursquare Tips Dataset**
Composed of user reviews in portuguese, referring to localities of São Paulo/Brazil and collected with the Foursquare API from the categories: Food, Shop & Service and Nightlife Spot. 

>```dataset_test.csv``` has a total of 179,181 reviews.
>
>```tips_scenario1_train.csv``` contains 1708 reviews labeled as **negative, neutral or positive**.
>
>```tips_scenario2_train.csv``` contains 1788 reviews labeled as **negative or positive**.


In [37]:
#@title
import chart_studio.plotly as py
import plotly.graph_objects as go
from plotly.subplots import make_subplots


path = 'https://raw.githubusercontent.com/eduartheinen/foursquare-tips/master/data/'

df1 = pd.read_csv(path + 'tips_scenario1_train.csv').dropna(how='any')
df2 = pd.read_csv(path + 'tips_scenario2_train.csv').dropna(how='any')

fig = make_subplots(rows=1, cols=2, shared_yaxes=True, subplot_titles=("Scenario 1","Scenario 2"))

fig.add_trace(go.Bar(x=['negative', 'neutral', 'positive'],
                     y=[len(df1[df1.rotulo==c]) for c in df1.rotulo.unique()],
                     marker_color=['red', 'gray', 'blue']),
              row=1, col=1)

fig.add_trace(go.Bar(x=['negative', 'positive'],
                     y=[len(df2[df2.rotulo==c]) for c in df2.rotulo.unique()],
                     marker_color=['red', 'blue']), 
              row=1, col=2)
    
fig.update_layout(autosize=False, showlegend=False, width=1000, height=500, title='Samples Distribution')

# **1. Data Preprocessing**

- Raw dataset entries contain a sentence of 30 words, followed by its label.

- After removing urls, punctuation marks and numbers, each sentence is processed with the **SpaCy NLP API**, trained in Portuguese.

- This step tokenizes and adds properties to each term of the sentence;

- Properties as:
>   **```lemma_```** return the word's canonical form, 
>
>   **```pos_```** it's part of speech tag (noun, verb, adjective, ...),
>
>   **```is_stop```** determine if it is a stop word.

- **For instance,** the sentence:
> "Eu fui morar na Estação da Luz. Porque estava muito escuro dentro do meu coração"

- **...would become**:
> ```tokens = ['morar', 'estação', 'luz', 'escuro', 'coração']```
>
> ```lemmas = ['morar', 'estação', 'luzir', 'escuro', 'coração']```
>
> ```pos = ['VERB', 'NOUN', 'NOUN', 'ADJ', 'NOUN']```

#**2. Feature Engineering**

One of the first fundamental choices involded in the construction of a Machine/Deep Learning Model is the representation of real world observations as features that can be read and understood by the model.

The **observations** in the dataset are **sentence with 30 words** followed by a **label** that indicates the **overall sentiment** of that sentence.

As the sentences are user reviews written in portuguese, they retain the subjective and flexible nature of colloquial language. Thus, an ideal machine learning model should be able to map not only the correlation between words and labels, but their context and it's effects on the sentence's meaning.

##2.1 Text Representation: Bag of Words and TF-IDF

![bow.png](https://i.imgur.com/TTjtkUH.png)

##2.2 Single Value Decomposition and Latent Semantic Analysis
![lsa.png](https://i.imgur.com/EMWATJX.png)


In [38]:
class FoursquareTipsDataset():
    def __init__(self, df, ngram_range=None):
        # extracting lemmas and POS tags with spacy even though we are not using them yet
        self.sentences, self.terms, self.lemmas, self.pos = self.preprocess(df.texto)
        self.labels = df.rotulo.reset_index(drop=True)
        self.feature_type_ = 'bow'

        self.vocab = Vocab(  # Collections.Counter for words in sentences
            Counter([str(term) for sentence in self.terms for term in sentence]))
        # min_freq=min_freq, specials=special_tags)

        # bag of words
        self.count_vectorizer = CountVectorizer(ngram_range=ngram_range)
        self.bow = self.count_vectorizer.fit_transform(self.sentences)

        # tfidf
        self.tfidf_vectorizer = TfidfVectorizer(ngram_range=ngram_range, max_df=0.99,
                                                min_df=0.002)  # removed if present in less than 3.6 documents
        self.tfidf = self.tfidf_vectorizer.fit_transform(self.sentences)

        # SVD/LSA
        print('fitting bow_lsa')
        # self.svd_bow = self.fit_svd_bow(self.bow)
        print('fitting tfidf_lsa')
        # self.svd_tfidf = self.fit_svd_tfidf(self.tfidf)

        # for easy indexing
        self.sentences = pd.DataFrame(self.sentences)
        self.terms = pd.DataFrame(self.terms)
        self.lemmas = pd.DataFrame(self.lemmas)
        self.pos = pd.DataFrame(self.pos)

    def feature_type(self, feature_type):
        self.feature_type_ = feature_type

    @staticmethod
    def preprocess(reviews):
        sentences = []
        lemmas = []
        pos = []
        terms = []

        for sentence in tqdm(reviews):
            sentence = re.sub(r'http\S+', '', sentence)  # removes urls before punctuation
            punctuation_to_space = str.maketrans(string.punctuation, ' ' * len(string.punctuation))
            sentence = sentence.translate(punctuation_to_space)  # change punctuations to spaces
            sentence = str.lower(sentence)
            sentence = re.sub('\d+', '', sentence)  # removes numbers
            sentence = re.sub(' +', ' ', sentence)  # removes double spaces

            # spacy processing -- nlp(sentence) -- adds properties to words,
            # like "lemma_", "pos_" and "is_stop" for stop_words.
            sentence = list(filter(lambda w: not w.is_stop, nlp(sentence)))
            lemmas.append([w.lemma_ for w in sentence if not w.is_stop])
            pos.append([w.pos_ for w in sentence if not w.is_stop])
            terms.append([str(w) for w in sentence if not w.is_stop])

            # sklearn count/tfidf vectorizers require raw text
            sentences.append(' '.join([w.text for w in sentence]))

        return sentences, terms, lemmas, pos

    def fit_svd_bow(self, data):
        for c in range(1400, 2000, 100):
            svd = TruncatedSVD(n_components=c, n_iter=10)
            svd.fit(data)
            if svd.explained_variance_ratio_.sum() > 0.98:
                break
        print(f'{c} components explained {svd.explained_variance_ratio_.sum():.4f} of feature variance.')
        return svd.fit_transform(data)

    def fit_svd_tfidf(self, data):
        for c in range(1, data.shape[1], 20):
            svd = TruncatedSVD(n_components=c, n_iter=10)
            svd.fit(data)
            if svd.explained_variance_ratio_.sum() > 0.98:
                break
        print(f'{c} components explained {svd.explained_variance_ratio_.sum():.4f} of feature variance.')
        return svd.fit_transform(data)

    def __getitem__(self, i):
        if self.feature_type_ == 'svd_tfidf':
            return self.svd_tfidf[i], self.labels.iloc[i]

        if self.feature_type_ == 'svd_bow':
            return self.svd_bow[i], self.labels.iloc[i]

        if self.feature_type_ == 'tfidf':
            return self.tfidf[i].toarray(), self.labels.iloc[i]

        if self.feature_type_ == 'sequence':
            return self.terms.iloc[i]. \
                       apply(lambda s: [self.vocab.stoi[t] for t in s]). \
                       reset_index(drop=True), \
                   self.labels.iloc[i].reset_index(drop=True)

        return self.bow[i].toarray(), self.labels.iloc[i]

    def __len__(self):
        return self.bow.shape[0]

##\<Load and Process Dataset\>

In [39]:
nlp = spacy.load('pt_core_news_sm')
nlp.Defaults.stop_words.add('a')
nlp.Defaults.stop_words.add('e')

path = 'https://raw.githubusercontent.com/eduartheinen/foursquare-tips/master/data/'

df = pd.read_csv(path + 'tips_scenario2_train.csv').dropna(how='any')
data = FoursquareTipsDataset(df, ngram_range=(1, 2))


fitting bow_lsa
fitting tfidf_lsa


## \<Validation Data\>
We set asside 0.15 of samples to validate and report models accuracy, precision, f1 score, recall and plot confusion matrixes.

- **accuracy**: exact matches between y_true and y_pred;
- **precision**: ```tp / (tp + fp)``` (intuitively) the ability not to label as positive a negative sample;
- **recall**:```tp / (tp + fn)``` (intuitively) the ability to find all the positive samples;
- **f1 score**: ```2 * (precision * recall) / (precision + recall)``` weighted average of precision and recall;

In [40]:
#@title
train_valid_split = int(len(data) * 0.85)  # excluding 0.15 for validation

In [41]:
def plot_analysis(accuracy, precision, recall, f1, model_name):

  features = ['bow', 'svd_bow', 'tfidf', 'svd_tfidf', 'bow_weighted', 'svd_bow_weighted', 'tfidf_weighted', 'svd_tfidf_weighted']
  class_names = ['negative', 'neutral', 'positive']
  class_colors = ['red', 'gray', 'blue']

  mean_accuracy = []
  mean_recall = []
  mean_precision = []
  mean_f1 = []

  # create figures
  fig1 = make_subplots(rows=1, cols=1)
  fig2 = make_subplots(rows=2, cols=4, shared_yaxes=True, subplot_titles=(features))
  fig3 = make_subplots(rows=2, cols=4, shared_yaxes=True, subplot_titles=(features))
  fig4 = make_subplots(rows=2, cols=4, shared_yaxes=True, subplot_titles=(features))

  col_counter = 1
  row_counter = 1

  for f in features:
    fig1.add_trace(go.Box(y=accuracy[f], name=f), row=1, col=1)
    mean_accuracy.append(np.mean(accuracy[f]))

    precision_feature = pd.DataFrame(precision[f])
    mean_precision.append([precision_feature.iloc[:, i].mean() for i in range(0,3)])  # another FOR

    recall_feature = pd.DataFrame(recall[f])
    mean_recall.append([recall_feature.iloc[:, i].mean() for i in range(0,3)])  # another FOR
    
    f1_feature = pd.DataFrame(f1[f])
    mean_f1.append([f1_feature.iloc[:, i].mean() for i in range(0,3)]) # and another FOR
    
    for c in range(0,3):
      fig2.add_trace(go.Box(y=precision_feature.iloc[:, c], name=class_names[c], marker_color=class_colors[c]), row=row_counter, col=col_counter)
      fig3.add_trace(go.Box(y=recall_feature.iloc[:, c], name=class_names[c], marker_color=class_colors[c]), row=row_counter, col=col_counter)
      fig4.add_trace(go.Box(y=f1_feature.iloc[:, c], name=class_names[c], marker_color=class_colors[c]), row=row_counter, col=col_counter)


    col_counter += 1
    if col_counter % 4 == 1:
      row_counter = 2 
      col_counter = 1


    fig1.update_layout(title=f'{model_name} Accuracy', showlegend=False, autosize=False, width=800, height=500)
    fig2.update_layout(title=f'{model_name} Precision', showlegend=False, autosize=False, width=1200, height=800)
    fig3.update_layout(title=f'{model_name} Recall', showlegend=False, autosize=False, width=1200, height=800)
    fig4.update_layout(title=f'{model_name} F1 Score', showlegend=False, autosize=False, width=1200, height=800)

  # out of fors
  return fig1, fig2, fig3, fig4, mean_accuracy, mean_precision, mean_recall, mean_f1


# fig1, fig2, fig3, fig4, mean_accuracy, mean_precision, mean_recall, mean_f1 = plot_analysis(accuracy, precision, recall, f1, 'SVC')
# fig1.show()

#Bi-directional LSTM

In [ ]:
"""#Bi-directional LSTM"""

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

hidden_dim = 24
learning_rate = 0.02
weight_decay = 0.02
max_epochs = 100


class BiLSTM(nn.Module):
    def __init__(self, input_dim, hidden_dim, num_classes):
        super(BiLSTM, self).__init__()
        self.input_dim = input_dim
        self.hidden_dim = hidden_dim
        self.num_classes = num_classes

        # GloVe, but contains only vectors that refer to words on the dataset vocabulary
        # self.word_embeds = nn.Embedding.from_pretrained(embedding_vectors)
        self.lstm = nn.LSTM(input_dim, hidden_dim // 2, num_layers=1, bidirectional=True, batch_first=True)

        # Maps the output of the LSTM into label space.
        self.hidden2label = nn.Linear(hidden_dim, num_classes)
        self.hidden = self.init_hidden()

    def init_hidden(self):
        return (torch.nn.init.xavier_uniform_(torch.zeros(2, 1, self.hidden_dim // 2)).to(device),
                torch.nn.init.xavier_uniform_(torch.zeros(2, 1, self.hidden_dim // 2)).to(device))

    def forward(self, sentence):
        self.hidden = self.init_hi
        dden()
        # as of batch_first=True requires input shape (batch, seq, feature)
        sentence = sentence.view(1, 1, len(sentence))
        lstm_out, _ = self.lstm(sentence, self.hidden)
        lstm_feats = self.hidden2label(lstm_out)
        labels = F.softmax(lstm_feats[0], dim=1)

        return labels

In [53]:
def training_epoch(model, optimizer, train_x, train_y):  # criterion, scheduler
    model.train()
    losses = []
    progress_bar = tqdm(train_x.index, desc='Training', leave=False)
    for i in progress_bar:
        inputs = torch.Tensor(train_x.iloc[i, :]).to(device)
        target = torch.LongTensor([0 if train_y[i] == -1 else 1]).to(device)

        # Clean old gradients
        # optimizer.zero_grad()
        model.zero_grad()

        # Forwards pass
        output = model(inputs)
        loss = criterion(output, target)

        # acc = accuracy_score(model, output)

        # Perform gradient descent, backwards pass
        loss.backward()

        # Take a step in the right direction
        optimizer.step()
        # scheduler.step()

        losses.append(loss.item())

    # plot_losses(losses, 'batch #', 'neg_log_likelihood_loss', 'Training Loss')
    return np.mean(losses)




def validate_epoch(model, test_x, test_y):  # criterion, scheduler
  model.eval()
  output = []
  targets = []
  accuracy = []
  precision = []
  recall = []
  f1 = []
  with torch.no_grad():
      progress_bar = tqdm(range(len(test_x)), desc='Validating', leave=False)
      for i in progress_bar:
          inputs = torch.Tensor(test_x.iloc[i, :]).to(device)

          # Forwards pass
          output.append(int(model(inputs).argmax()))  # TODO: save only data, ignore tensors
          targets.append(0 if test_y[i] == -1 else 1)

      # Calculating the F-Score
      accuracy.append(accuracy_score(targets, output))
      precision.append(precision_score(targets, output, zero_division=1))
      recall.append(recall_score(targets, output))
      f1.append(f1_score(targets, output))

  return np.mean(accuracy), np.mean(precision), np.mean(recall), np.mean(f1)

In [ ]:
model = BiLSTM(data.terms.shape[1], hidden_dim, 2).to(device)
optimizer = optim.AdamW(filter(lambda p: p.requires_grad, model.parameters()),
                        lr=learning_rate, weight_decay=weight_decay)
# optimizer = optim.SGD(model.parameters(), lr=learning_rate, weight_decay=weight_decay)
criterion = nn.CrossEntropyLoss().to(device)

best_F = 0
epoch = 0


# training epochs
data.feature_type('sequence')
kf = KFold(n_splits=5, shuffle=True)
for train_index, test_index in kf.split(data.bow):
    for epoch in range(max_epochs):
        train_x, train_y = data[train_index]
        test_x, test_y = data[test_index]

        train_loss = training_epoch(model, optimizer, train_x, train_y)  # train_loader
        accuracy, precision, recall, f1  = validate_epoch(model, test_x, test_y)

        tqdm.write(
            f'\nepoch #{epoch + 1:3d}\ttrain_loss: {train_loss:.6f}\taccuracy: {accuracy:.6f}\tprecision: {precision:.6f}\trecall: {recall:.6f}\tf1: {f1:.6f}')



Training:  94%|█████████▍| 1345/1430 [1:22:09<00:00, 322.67it/s]


epoch #  1	train_loss: 0.566200	accuracy: 0.483240	precision: 1.000000	recall: 0.000000	f1: 0.000000



Training:  94%|█████████▍| 1345/1430 [1:22:14<00:00, 322.67it/s]


epoch #  2	train_loss: 0.603510	accuracy: 0.483240	precision: 1.000000	recall: 0.000000	f1: 0.000000



Training:  94%|█████████▍| 1345/1430 [1:22:19<00:00, 322.67it/s]

...


epoch # 10	train_loss: 0.606064	accuracy: 0.456583	precision: 1.000000	recall: 0.000000	f1: 0.000000



Training:  94%|█████████▍| 1345/1430 [2:09:23<00:00, 322.67it/s]


epoch # 11	train_loss: 0.605641	accuracy: 0.456583	precision: 1.000000	recall: 0.000000	f1: 0.000000



Training:  94%|█████████▍| 1345/1430 [2:09:32<00:00, 322.67it/s]


epoch # 12	train_loss: 0.559590	accuracy: 0.456583	precision: 1.000000	recall: 0.000000	f1: 0.000000
